# Hyperparameter optimization for Neural Network Models

In [3]:
import yfinance as yf
import ta
from sklearn.ensemble import RandomForestRegressor
from darts import TimeSeries
from darts.dataprocessing.transformers import Scaler
from darts import concatenate
import numpy as np
import torch
from pytorch_lightning.callbacks import EarlyStopping
from darts.models import TCNModel, BlockRNNModel, TransformerModel, TFTModel, NBEATSModel
from darts.metrics import mae


torch.manual_seed(1)
np.random.seed(1)

/usr/local/lib/python3.10/dist-packages/yfinance/base.py:48: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  _empty_series = pd.Series()


# Code to Fix PytorchLightningPruningCallBack Bug for Optuna

In [4]:
from pytorch_lightning import LightningModule
from pytorch_lightning import Trainer
from pytorch_lightning.callbacks import Callback
import optuna
import warnings

class PyTorchLightningPruningCallback(Callback):
    """PyTorch Lightning callback to prune unpromising trials.
    See `the example <https://github.com/optuna/optuna-examples/blob/
    main/pytorch/pytorch_lightning_simple.py>`__
    if you want to add a pruning callback which observes accuracy.
    Args:
        trial:
            A :class:`~optuna.trial.Trial` corresponding to the current evaluation of the
            objective function.
        monitor:
            An evaluation metric for pruning, e.g., ``val_loss`` or
            ``val_acc``. The metrics are obtained from the returned dictionaries from e.g.
            ``pytorch_lightning.LightningModule.training_step`` or
            ``pytorch_lightning.LightningModule.validation_epoch_end`` and the names thus depend on
            how this dictionary is formatted.
    """

    def __init__(self, trial: optuna.trial.Trial, monitor: str) -> None:
        super().__init__()

        self._trial = trial
        self.monitor = monitor

    def on_validation_end(self, trainer: Trainer, pl_module: LightningModule) -> None:
        # When the trainer calls `on_validation_end` for sanity check,
        # do not call `trial.report` to avoid calling `trial.report` multiple times
        # at epoch 0. The related page is
        # https://github.com/PyTorchLightning/pytorch-lightning/issues/1391.
        if trainer.sanity_checking:
            return

        epoch = pl_module.current_epoch

        current_score = trainer.callback_metrics.get(self.monitor)
        if current_score is None:
            message = (
                "The metric '{}' is not in the evaluation logs for pruning. "
                "Please make sure you set the correct metric name.".format(self.monitor)
            )
            warnings.warn(message)
            return

        self._trial.report(current_score, step=epoch)
        if self._trial.should_prune():
            message = "Trial was pruned at epoch {}.".format(epoch)
            raise optuna.TrialPruned(message)

# Retrieve Bitcoin data

In [5]:
#retrieve bitcoin data
start_date = '2014-09-17'
end_date = '2024-01-23'

df = yf.download('BTC-USD', interval = '1d', start = start_date, end = end_date)
df = df.drop('Adj Close', axis=1)
df = ta.utils.dropna(df)
df = ta.add_all_ta_features(
    df, "Open", "High", "Low", "Close", "Volume", fillna=True
)
df = df.fillna(0)

[*********************100%%**********************]  1 of 1 completed


# Feature engineering

In [6]:
split_index = int(len(df) * 0.8)  # 80% for training, 20% for testing
X_train = df.iloc[:split_index].drop('Close', axis=1)
y_train = df.iloc[:split_index]['Close']
X_test = df.iloc[split_index:].drop('Close', axis=1)
y_test = df.iloc[split_index:]['Close']

In [7]:
clf = RandomForestRegressor(n_jobs=-1)
clf.fit(X_train, y_train)

RandomForestRegressor(n_jobs=-1)

In [8]:
clf.score(X_test, y_test)

0.9390639591506529

In [9]:
features = {k: v for k, v in sorted(zip(X_train.columns, clf.feature_importances_), key=lambda x: x[1], reverse=True)}

In [10]:
filtered_features = {feature: importance for feature, importance in features.items() if importance >= 0.01}

In [11]:
filtered_feature_names = list(filtered_features.keys())
df = df.reset_index()
covs= TimeSeries.from_dataframe(df, time_col="Date", value_cols=filtered_feature_names)
covs = covs.astype(np.float32)
target = TimeSeries.from_dataframe(df, time_col="Date", value_cols=["Close"])
target = target.astype(np.float32)

# Create Train, Validation and Test Set + Past and Future Covariates

In [12]:
#create train and validation series and scale them
val_set_size = 28

test_set_size = 365

train_target = target[: -(val_set_size + test_set_size)]

val_target = target[-(val_set_size + test_set_size) : -test_set_size]

test_target = target[-(test_set_size) :]

scaler_target = Scaler()
scaler_features = Scaler()

scaler_target = scaler_target.fit(train_target)


train_scaled = scaler_target.transform(train_target)
val_scaled = scaler_target.transform(val_target)
test_scaled = scaler_target.transform(test_target)

target_scaled = concatenate([train_target, val_target])


In [15]:
val = scaler_target.inverse_transform(val_scaled)

# GRU Model + Optuna Optimization

In [17]:
def build_fit_GRU_model(
    in_len,
    out_len,
    hidden_dim,
    n_rnn_layers,
    dropout,
    include_encoders,
    lr,
    callbacks = None
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available
    if torch.cuda.is_available():
        pl_trainer_kwargs = {
            "accelerator": "gpu",
            "callbacks": callbacks,
        }
        num_workers = 2
    else:
        pl_trainer_kwargs = {"callbacks": callbacks}
        num_workers = 0

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'past': ['day', 'week', 'year']},
        'position': {'past': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = BlockRNNModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        model='GRU',
        hidden_dim = hidden_dim,
        n_rnn_layers= n_rnn_layers,
        n_epochs=100,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="GRUmodel",
        save_checkpoints=True,
        force_reset = True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = BlockRNNModel.load_from_checkpoint("GRUmodel")

    return model

In [18]:
def objective_GRU(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    hidden_dim = trial.suggest_int('hidden_dim', 20, 200)
    n_rnn_layers = trial.suggest_int('r_rnn_layers', 1, 5)
    dropout = trial.suggest_float("dropout", 0.0, 0.5)
    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_GRU_model(
        in_len=days_in,
        out_len=days_out,
        hidden_dim=hidden_dim,
        n_rnn_layers=n_rnn_layers,
        dropout=dropout,
        lr=lr,
        include_encoders=include_encoders,
        callbacks=callback,
    )



    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [19]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_GRU, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

Current value: 0.0022769172210246325, Current params: {'hidden_dim': 157, 'r_rnn_layers': 3, 'dropout': 0.45965230518879313, 'lr': 0.00026805280056627046, 'encoders': False}
Best value: 1208.449951171875, Best params: {'hidden_dim': 153, 'r_rnn_layers': 3, 'dropout': 0.13679103330711126, 'lr': 0.000514872981922757, 'encoders': False}


INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | GRU              | 506 K 
4 | fc            | Sequential       | 1.3 K 
---------------------------------------------------
507 K     Trainable params
0         Non-trainable params
507 K     Total params
2.030     Total estimated model params size (MB)


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 5 records. Best score: 0.002. Signaling Trainer to stop.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]



100%|██████████| 1/1 [00:00<00:00, 725.16it/s]
[I 2024-02-03 11:57:58,400] Trial 99 finished with value: 1486.810791015625 and parameters: {'hidden_dim': 89, 'r_rnn_layers': 4, 'dropout': 0.19798654867538484, 'lr': 0.0002780824717800229, 'encoders': False}. Best is trial 10 with value: 1344.340087890625.


Current value: 1486.810791015625, Current params: {'hidden_dim': 89, 'r_rnn_layers': 4, 'dropout': 0.19798654867538484, 'lr': 0.0002780824717800229, 'encoders': False}
Best value: 1344.340087890625, Best params: {'hidden_dim': 75, 'r_rnn_layers': 1, 'dropout': 0.007824503730612165, 'lr': 0.000566687831423731, 'encoders': False}
Best value: 1344.340087890625, Best params: {'hidden_dim': 75, 'r_rnn_layers': 1, 'dropout': 0.007824503730612165, 'lr': 0.000566687831423731, 'encoders': False}


In [20]:
study.best_trial.params

{'hidden_dim': 75,
 'r_rnn_layers': 1,
 'dropout': 0.007824503730612165,
 'lr': 0.000566687831423731,
 'encoders': False}

# TFT Model + Optuna optimization

In [ ]:
def build_fit_TFT_model(
    in_len,
    out_len,
    hidden_size,
    lstm_layers,
    num_attention_heads,
    hidden_continuous_size,
    dropout,
    lr,
    include_encoders,
    callbacks=None,
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks


    pl_trainer_kwargs = {"callbacks": callbacks}
    num_workers = 2

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'future': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'future': ['day', 'week', 'year']},
        'position': {'past': ['relative'], 'future': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = TFTModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        hidden_size = hidden_size,
        lstm_layers = lstm_layers,
        num_attention_heads = num_attention_heads,
        hidden_continuous_size = hidden_continuous_size,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="TFTmodel",
        force_reset=True,
        save_checkpoints=True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = TFTModel.load_from_checkpoint("TFTmodel")

    return model

In [ ]:
def objective_TFT(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    hidden_size = trial.suggest_int('hidden_size', 16, 32)
    lstm_layers = trial.suggest_int('lstm_layers', 1, 3)
    num_attention_heads = trial.suggest_int('num_attention_heads', 1, 4)
    dropout = trial.suggest_float('dropout', 0.0, 0.3)
    hidden_continuous_size = trial.suggest_int('hidden_continuous_size', 8, 12)
    lr = trial.suggest_float("lr", 1e-4, 1e-2, log=True)
    #include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_TFT_model(
        in_len = days_in,
        out_len = days_out,
        hidden_size = hidden_size,
        lstm_layers = lstm_layers,
        num_attention_heads = num_attention_heads,


        hidden_continuous_size = hidden_continuous_size,
        dropout=dropout,
        lr = lr,
        include_encoders = True,
        callbacks=callback,
    )

    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_TFT, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

[I 2024-01-25 21:38:31,777] A new study created in memory with name: no-name-a0aea8df-330b-4772-9048-e1904cbada9f
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
   | Name                              | Type                             | Params
----------------------------------------------------------------------------------------
0  | train_metrics                     | MetricCollection                 | 0     
1  | val_metrics                       | MetricCollection                 | 0     
2  | input_embeddings                  | _MultiEmbedding                  | 0     
3  | stati

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 1.267


...

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

[I 2024-01-25 22:27:45,665] Trial 99 pruned. Trial was pruned at epoch 0.


Current value: 0.618495762348175, Current params: {'hidden_size': 28, 'lstm_layers': 1, 'num_attention_heads': 1, 'dropout': 0.028211984345444564, 'hidden_continuous_size': 10, 'lr': 0.0015701272419559895}
Best value: 1763.4486083984375, Best params: {'hidden_size': 30, 'lstm_layers': 1, 'num_attention_heads': 4, 'dropout': 0.06118422728497173, 'hidden_continuous_size': 10, 'lr': 0.005081664304452033}
Best value: 1763.4486083984375, Best params: {'hidden_size': 30, 'lstm_layers': 1, 'num_attention_heads': 4, 'dropout': 0.06118422728497173, 'hidden_continuous_size': 10, 'lr': 0.005081664304452033}


In [ ]:
study.best_trial.params

{'hidden_size': 30,
 'lstm_layers': 1,
 'num_attention_heads': 4,
 'dropout': 0.06118422728497173,
 'hidden_continuous_size': 10,
 'lr': 0.005081664304452033}

# LSTM + Optuna optimization

In [ ]:
def build_fit_LSTM_model(
    in_len,
    out_len,
    hidden_dim,
    n_rnn_layers,
    dropout,
    include_encoders,
    lr,
    callbacks = None
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available
    if torch.cuda.is_available():
        pl_trainer_kwargs = {
            "accelerator": "gpu",
            "callbacks": callbacks,
        }
        num_workers = 2
    else:
        pl_trainer_kwargs = {"callbacks": callbacks}
        num_workers = 0

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'past': ['day', 'week', 'year']},
        'position': {'past': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = BlockRNNModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        model='LSTM',
        hidden_dim = hidden_dim,
        n_rnn_layers= n_rnn_layers,
        n_epochs=100,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="LSTMmodel",
        save_checkpoints=True,
        force_reset = True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = BlockRNNModel.load_from_checkpoint("LSTMmodel")

    return model

In [ ]:
def objective_LSTM(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    hidden_dim = trial.suggest_int('hidden_dim', 20, 200)
    n_rnn_layers = trial.suggest_int('r_rnn_layers', 1, 5)
    dropout = trial.suggest_float("dropout", 0.0, 0.5)
    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_LSTM_model(
        in_len=days_in,
        out_len=days_out,
        hidden_dim=hidden_dim,
        n_rnn_layers=n_rnn_layers,
        dropout=dropout,
        lr=lr,
        include_encoders=include_encoders,
        callbacks=callback,
    )



    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_LSTM, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

[I 2024-01-25 23:37:22,761] A new study created in memory with name: no-name-29090e67-a2c7-4fe2-89f5-b58eeb288e36
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | LSTM             | 281 K 
4 | fc            | Sequential       | 700   
---------------------------------------------------
282 K     Trainable params
0         Non-trainable 

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.061


...

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

[I 2024-01-25 23:57:45,815] Trial 99 pruned. Trial was pruned at epoch 0.


Current value: 0.002663614694029093, Current params: {'hidden_dim': 155, 'r_rnn_layers': 4, 'dropout': 0.25598035876611747, 'lr': 4.728456478932595e-05, 'encoders': True}
Best value: 2140.15185546875, Best params: {'hidden_dim': 104, 'r_rnn_layers': 4, 'dropout': 0.18390991552139796, 'lr': 0.00014678997505613995, 'encoders': False}
Best value: 2140.15185546875, Best params: {'hidden_dim': 104, 'r_rnn_layers': 4, 'dropout': 0.18390991552139796, 'lr': 0.00014678997505613995, 'encoders': False}


In [ ]:
study.best_trial.params

{'hidden_dim': 104,
 'r_rnn_layers': 4,
 'dropout': 0.18390991552139796,
 'lr': 0.00014678997505613995,
 'encoders': False}

# VanillaRNN Model + Optuna optimization

In [ ]:
def build_fit_VanillaRNN_model(
    in_len,
    out_len,
    hidden_dim,
    n_rnn_layers,
    dropout,
    include_encoders,
    lr,
    callbacks = None
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available
    if torch.cuda.is_available():
        pl_trainer_kwargs = {
            "accelerator": "gpu",
            "callbacks": callbacks,
        }
        num_workers = 2
    else:
        pl_trainer_kwargs = {"callbacks": callbacks}
        num_workers = 0

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'past': ['day', 'week', 'year']},
        'position': {'past': ['relative'],},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = BlockRNNModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        model='RNN',
        hidden_dim = hidden_dim,
        n_rnn_layers= n_rnn_layers,
        n_epochs=100,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="RNN",
        force_reset=True,
        save_checkpoints=True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = BlockRNNModel.load_from_checkpoint("RNN")

    return model

In [ ]:
def objective_VanillaRNN(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    hidden_dim = trial.suggest_int('hidden_dim', 10, 100)
    n_rnn_layers = trial.suggest_int('n_rnn_layers', 1, 5)
    dropout = trial.suggest_float("dropout", 0.0, 0.5)
    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_VanillaRNN_model(
        in_len=days_in,
        out_len=days_out,
        hidden_dim=hidden_dim,
        n_rnn_layers=n_rnn_layers,
        dropout=dropout,
        lr=lr,
        include_encoders=include_encoders,
        callbacks=callback,
    )

    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_VanillaRNN, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

[I 2024-01-26 01:43:31,889] A new study created in memory with name: no-name-198d1541-1ea7-4433-83ba-991f13c9947b
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | rnn           | RNN              | 27.5 K
4 | fc            | Sequential       | 441   
---------------------------------------------------
27.9 K    Trainable params
0         Non-trainable 

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.013


...

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

[I 2024-01-26 01:59:30,299] Trial 99 pruned. Trial was pruned at epoch 0.


Current value: 0.008858350105583668, Current params: {'hidden_dim': 22, 'n_rnn_layers': 1, 'dropout': 0.17606340235643667, 'lr': 0.0005784636458486539, 'encoders': False}
Best value: 1282.8416748046875, Best params: {'hidden_dim': 31, 'n_rnn_layers': 1, 'dropout': 0.34008569567908437, 'lr': 0.0009241588491743642, 'encoders': False}
Best value: 1282.8416748046875, Best params: {'hidden_dim': 31, 'n_rnn_layers': 1, 'dropout': 0.34008569567908437, 'lr': 0.0009241588491743642, 'encoders': False}


In [ ]:
study.best_trial.params

{'hidden_dim': 31,
 'n_rnn_layers': 1,
 'dropout': 0.34008569567908437,
 'lr': 0.0009241588491743642,
 'encoders': False}

# Transformer Model + Optuna optimization

Best params: {'d_model': 88,
 'nhead': 4,
 'num_encoder_layers': 4,
 'num_decoder_layers': 1,
 'dropout': 0.14295488378943239,
 'lr': 0.00046254166100837376,
 'encoders': False}

In [ ]:
def build_fit_transformer_model(
    in_len,
    out_len,
    d_model,
    nhead,
    num_encoder_layers,
    num_decoder_layers,
    dropout,
    lr,
    include_encoders,
    callbacks=None,
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available
    if torch.cuda.is_available():
        pl_trainer_kwargs = {
            "accelerator": "gpu",
            "gpus": -1,
            "auto_select_gpus": True,
            "callbacks": callbacks,
        }
        num_workers = 4
    else:
        pl_trainer_kwargs = {"callbacks": callbacks}
        num_workers = 0

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'future': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'future': ['day', 'week', 'year']},
        'position': {'past': ['relative'], 'future': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = TransformerModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        d_model = d_model,
        nhead = nhead,
        num_encoder_layers = num_encoder_layers,
        num_decoder_layers = num_decoder_layers,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="transformermodel",
        force_reset=True,
        save_checkpoints=True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = TransformerModel.load_from_checkpoint("transformermodel")

    return model

In [ ]:
def objective_Transformer(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    d_model = trial.suggest_categorical('d_model', [64, 68, 72, 76, 80, 84, 88, 92, 96])
    nhead = trial.suggest_categorical('nhead', [2, 4])
    num_encoder_layers = trial.suggest_int('num_encoder_layers', 1, 4)
    num_decoder_layers = trial.suggest_int('num_decoder_layers', 1, 4)


    dropout = trial.suggest_float("dropout", 0.1, 0.5)
    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_transformer_model(
        in_len = days_in,
        out_len = days_out,
        d_model = d_model,
        nhead = nhead,
        num_encoder_layers = num_encoder_layers,
        num_decoder_layers = num_decoder_layers,
        dropout = dropout,
        lr = lr,
        include_encoders = include_encoders,
        callbacks=callback,
    )

    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_Transformer, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

In [ ]:
study.best_trial.params

# NBEATS Model + Optuna optimization

Best parameters: {'num_stacks': 19,
 'num_blocks': 4,
 'num_layers': 4,
 'layer_widths': 378,
 'expansion_coefficient_dim': 8,
 'dropout': 0.007293860107310261,
 'lr': 0.0005903374698873167,
 'encoders': True}

In [ ]:
def build_fit_NBEATS_model(
    in_len,
    out_len,
    num_stacks,
    num_blocks,
    num_layers,
    layer_widths,
    expansion_coefficient_dim,
    dropout,
    lr,
    include_encoders,
    callbacks=None,
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available

    pl_trainer_kwargs = {"callbacks": callbacks}
    num_workers = 2

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'past': ['day', 'week', 'year']},
        'position': {'past': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = NBEATSModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        n_epochs=100,
        num_stacks=num_stacks,
        num_blocks=num_blocks,
        num_layers=num_layers,
        layer_widths=layer_widths,
        expansion_coefficient_dim=expansion_coefficient_dim,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="NBEATSmodel",
        save_checkpoints=True,
        force_reset = True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = NBEATSModel.load_from_checkpoint("NBEATSmodel")

    return model

In [ ]:
def objective_NBEATS(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    num_stacks = trial.suggest_int('num_stacks', 10, 30)
    num_blocks = trial.suggest_int('num_blocks', 1, 5)
    num_layers = trial.suggest_int('num_layers', 2, 4)
    layer_widths = trial.suggest_int('layer_widths', 128, 512)

    expansion_coefficient_dim = trial.suggest_int('expansion_coefficient_dim', 3, 10)
    dropout = trial.suggest_float('dropout', 0.0, 0.3)

    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_NBEATS_model(
        in_len = days_in,
        out_len = days_out,
        num_stacks = num_stacks,
        num_blocks = num_blocks,
        num_layers = num_layers,
        layer_widths = layer_widths,
        expansion_coefficient_dim = expansion_coefficient_dim,
        dropout = dropout,
        lr = lr,
        include_encoders = include_encoders,
        callbacks = callback,
    )

    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective_NBEATS, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

[I 2024-01-25 21:04:47,406] A new study created in memory with name: no-name-912357b5-f1ec-4225-ac01-0c62ee70ba8e
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type             | Params
---------------------------------------------------
0 | criterion     | MSELoss          | 0     
1 | train_metrics | MetricCollection | 0     
2 | val_metrics   | MetricCollection | 0     
3 | stacks        | ModuleList       | 42.5 M
---------------------------------------------------
42.5 M    Trainable params
2.2 K     Non-trainable params
42.5 M    Total params
170.021   Total 

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.009


...

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Monitored metric val_loss did not improve in the last 5 records. Best score: 0.001. Signaling Trainer to stop.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

100%|██████████| 1/1 [00:00<00:00, 560.14it/s]
[I 2024-01-25 22:28:07,760] Trial 99 finished with value: 4182.33056640625 and parameters: {'num_stacks': 11, 'num_blocks': 4, 'num_layers': 4, 'layer_widths': 360, 'expansion_coefficient_dim': 7, 'dropout': 0.015450595014399026, 'lr': 3.643281189237905e-05, 'encoders': False}. Best is trial 63 with value: 1333.672607421875.


Current value: 4182.33056640625, Current params: {'num_stacks': 11, 'num_blocks': 4, 'num_layers': 4, 'layer_widths': 360, 'expansion_coefficient_dim': 7, 'dropout': 0.015450595014399026, 'lr': 3.643281189237905e-05, 'encoders': False}
Best value: 1333.672607421875, Best params: {'num_stacks': 19, 'num_blocks': 4, 'num_layers': 4, 'layer_widths': 378, 'expansion_coefficient_dim': 8, 'dropout': 0.007293860107310261, 'lr': 0.0005903374698873167, 'encoders': True}
Best value: 1333.672607421875, Best params: {'num_stacks': 19, 'num_blocks': 4, 'num_layers': 4, 'layer_widths': 378, 'expansion_coefficient_dim': 8, 'dropout': 0.007293860107310261, 'lr': 0.0005903374698873167, 'encoders': True}


In [ ]:
study.best_trial.params

{'num_stacks': 19,
 'num_blocks': 4,
 'num_layers': 4,
 'layer_widths': 378,
 'expansion_coefficient_dim': 8,
 'dropout': 0.007293860107310261,
 'lr': 0.0005903374698873167,
 'encoders': True}

# TCN Model + Optuna optimization

In [ ]:
def build_fit_tcn_model(
    in_len,
    out_len,
    kernel_size,
    num_filters,
    weight_norm,
    dilation_base,
    dropout,
    lr,
    include_encoders,
    likelihood=None,
    callbacks=None,
):

    # reproducibility
    torch.manual_seed(42)

    # throughout training we'll monitor the validation loss for early stopping
    early_stopper = EarlyStopping("val_loss", min_delta=0.001, patience=5, verbose=True)

    if callbacks is None:
        callbacks = [early_stopper]
    else:
        callbacks = [early_stopper] + callbacks

    # detect if a GPU is available
    if torch.cuda.is_available():
        pl_trainer_kwargs = {
            "accelerator": "gpu",
            "callbacks": callbacks,
        }
        num_workers = 2
    else:
        pl_trainer_kwargs = {"callbacks": callbacks}
        num_workers = 0

    # optionally also add the day of the week (cyclically encoded) as a past covariate
    encoders = {
        'cyclic': {'past': ['month', 'dayofweek', 'dayofyear']},  # Capture seasonal trends
        'datetime_attribute': {'past': ['day', 'week', 'year']},
        'position': {'past': ['relative']},
        'transformer': Scaler(),
    } if include_encoders else None


    # build the TCN model
    model = TCNModel(
        input_chunk_length=in_len,
        output_chunk_length=out_len,
        n_epochs=100,
        kernel_size=kernel_size,
        num_filters=num_filters,
        weight_norm=weight_norm,
        dilation_base=dilation_base,
        dropout=dropout,
        optimizer_kwargs={"lr": lr},
        add_encoders=encoders,
        likelihood=likelihood,
        pl_trainer_kwargs=pl_trainer_kwargs,
        model_name="tcnmodel",
        force_reset=True,
        save_checkpoints=True,
    )


    # train the model
    model.fit(
        series=train_scaled,
        val_series=val_scaled,
        num_loader_workers=num_workers,
    )

    # reload best model over course of training
    model = TCNModel.load_from_checkpoint("tcnmodel")

    return model

In [ ]:
from darts.metrics import mae

def objective(trial):
    callback = [PyTorchLightningPruningCallback(trial, monitor="val_loss")]

    days_in = 21
    days_out = 7

    #num_layers = trial.suggest_int("num_layers", 2, 15)

    kernel_size = trial.suggest_int("kernel_size", 3, 10)
    num_filters = trial.suggest_int("num_filters", 10, 50)
    weight_norm = trial.suggest_categorical("weight_norm", [False, True])
    dilation_base = trial.suggest_int("dilation_base", 2, 8)
    dropout = trial.suggest_float("dropout", 0.0, 0.5)
    lr = trial.suggest_float("lr", 1e-5, 1e-3, log=True)
    include_encoders = trial.suggest_categorical("encoders", [False, True])


    # build and train the TCN model with these hyper-parameters:
    model = build_fit_tcn_model(
        in_len=days_in,
        out_len=days_out,
        kernel_size=kernel_size,
        num_filters=num_filters,
        weight_norm=weight_norm,
        dilation_base=dilation_base,
        dropout=dropout,
        lr=lr,
        include_encoders=include_encoders,
        callbacks=callback,
    )

    # Evaluate how good it is on the validation set
    pred = model.predict(series=train_scaled, n=len(val_scaled))
    pred = scaler_target.inverse_transform(pred)
    error = mae(val, pred, n_jobs=-1, verbose=True)

    return error if error != np.nan else float("inf")

In [ ]:
def print_callback(study, trial):
    print(f"Current value: {trial.value}, Current params: {trial.params}")
    print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")


study = optuna.create_study(direction="minimize")

study.optimize(objective, timeout=7200, n_trials = 100, callbacks=[print_callback])

print(f"Best value: {study.best_value}, Best params: {study.best_trial.params}")

[I 2024-01-25 23:03:43,607] A new study created in memory with name: no-name-3b0962af-4929-4e50-a6db-e3a310379a87
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name          | Type              | Params
----------------------------------------------------
0 | criterion     | MSELoss           | 0     
1 | train_metrics | MetricCollection  | 0     
2 | val_metrics   | MetricCollection  | 0     
3 | dropout       | MonteCarloDropout | 0     
4 | res_blocks    | ModuleList        | 10.9 K
----------------------------------------------------
10.9 K    Trainable params
0         Non-tr

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.callbacks.early_stopping:Metric val_loss improved. New best score: 0.167


...

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

[I 2024-01-25 23:27:58,612] Trial 99 pruned. Trial was pruned at epoch 0.


Current value: 0.01030823215842247, Current params: {'kernel_size': 10, 'num_filters': 38, 'weight_norm': False, 'dilation_base': 2, 'dropout': 0.11312978529198973, 'lr': 0.0008934814323122176, 'encoders': True}
Best value: 1180.1063232421875, Best params: {'kernel_size': 8, 'num_filters': 36, 'weight_norm': False, 'dilation_base': 2, 'dropout': 0.14321708644925318, 'lr': 0.0005056311276120884, 'encoders': True}
Best value: 1180.1063232421875, Best params: {'kernel_size': 8, 'num_filters': 36, 'weight_norm': False, 'dilation_base': 2, 'dropout': 0.14321708644925318, 'lr': 0.0005056311276120884, 'encoders': True}


In [ ]:
study.best_trial.params

{'kernel_size': 8,
 'num_filters': 36,
 'weight_norm': False,
 'dilation_base': 2,
 'dropout': 0.14321708644925318,
 'lr': 0.0005056311276120884,
 'encoders': True}